---

# S01E03 : The import system - Namespaces & scopes

Cyril Desjouy

---


## 1. A few reminders about names

A name is an **identifier** commonly called variable or variable name. It is a named location to access an object in memory. When writing `a = 1`, the identifier is assigned an object created by the interpreter whose value is `1` and its in-memory address (its identity) can be determined using the built-in `id` function.


<div class="alert alert-block alert-info">
Declare two variables <code>a</code> and <code>b</code> equal to 1 and compare the identity of these two objects.
</div>

The two objects have the same identity. This means that the identifiers `a` and `b` refer to the same object and that the Python interpreter has not duplicated in memory the integer type object with the value 1.

<div class="alert alert-block alert-info">
Now change the value of <code>b</code> by typing <code>b = b + 1</code> and compare again the identity of <code>a</code> and <code>b</code>.
</div>

A new integer object of type 2 has been created in memory. The variable `b` now refers to this new object.

<div class="alert alert-block alert-info">
Now create a module that you name <code>module</code> containing only the instruction <code>a = 1</code> then import this module into the notebook. Compare the identity of the identifiers <code>a</code> and <code>module.a</code>. Conclude.
</div>

In [ ]:
import module

id(a) == id(module.a)

**Note:** *To access an identifier of a module, it is prefixed by the name of the module as it was imported: `module.a`.*

## 2. Namespaces and scopes

We have already discussed the notion of ***namespace*** earlier when studying the modules. As a reminder, a ***namespace*** is a name container referencing objects. It is important to emphasize that a namespace does not contain objects, but only references to these objects, i.e. names. It should also be noted that, as seen above, it is possible to have several names, **which can be distributed in several namespaces**, referencing the same object. 

***namespaces*** are created by modules, functions, classes, ... Several ***namespaces*** can coexist at the same time but are totally isolated from each other. This allows you to have the same name in different namespaces without causing a collision. For example:

In [1]:
reset -f

In [ ]:
import numpy

class cls:
    def __init__(self):
        self.e = 'class'
        
def fct1():
    e = 'fct1'
    return e

def fct2():
    e = 'fct2'
    return e

if __name__ == '__main__':

    e = 'global'

    print('From numpy:', numpy.e)
    print('From cls:', cls().e)
    print('From fct1:', fct1())
    print('From fct2:', fct2())
    print('From program:', e)


The name `e` is defined in the `numpy` module, in the `cls` class, in the `fct1` and `fct2` functions and at the main program level without causing a collision. This is possible thanks to the *namespaces*. 

Even if it is possible to have several namespaces defined at the same time, it is not necessarily possible to access all these namespaces from any part of the program. This is called ***scope***. The ***scope*** is the part of the program from which it is possible to access a namespace without using a prefix (the prefix can be a name of a module for example: `numpy.e`, or a class instance, for example `cls().e` as seen above).

Under Python, there are 4 types of namespaces that each have their own ***scope***:

* **Local:** Names that are defined in a function.
* **Enclosed:** Names that are defined in a **closure** (i.e. a function in a function).
* **Global:** Names that are assigned to the file top-level, for example in your main program or in a module.
* **Built-in:** Names that are the Python built-ins (such as `print`, `return`, `import`, ...). This namespace is created when the Python interpreter starts and exists until it exits.

These different scopes are illustrated in Figure 1. 

```
______________________________________________________________
|######################### Built-in #########################|
|                                                            |
|    _____________________________________________________   |
|    |############## Global (module level) ##############|   |
|    |                                                   |   |
|    |   _____________________________________________   |   |
|    |   |##### Enclosed (function in function) #####|   |   |
|    |   |                                           |   |   |
|    |   |  ______________________________________   |   |   |
|    |   |  |###### Local (function level) ######|   |   |   |
|    |   |  |                                    |   |   |   |
|    |   |  |____________________________________|   |   |   |
|    |   |___________________________________________|   |   |
|    |___________________________________________________|   |
|____________________________________________________________|
              Fig. 1: Organisation of the namespace
```

The initials of these 4 ***namespaces/scopes*** form the **LEGB** rule (<b>L</b>ocal, <b>E</b>nclosed, <b>G</b>lobal, <b>B</b>uilt-in) which imposes the order in which namespaces are searched. 

The **LEGB** rule is formalized as follows:

* The lowest scope is **Local**, the highest is **Built-in**
* The lowest scopes can always access the highest scopes
* The highest scopes can never ***directly*** access the lowest scopes

It is because the highest scope is **Built-in** that the built-in functions are available in any part of the program. To illustrate this, let us consider a ***global space***. You can create identifiers referencing objects and also use names from the ***Built-in namespace***. Without ***global namespace*** you couldn't write this:

```python  
msg = "global"     # msg defined in a global namespace
print(msg)         # In the global namespace, you can access "print" function (Built-in namespace)
```

The functions have separate namespaces which are ***local namespace***. Each function has its own *namespace*.

```python
def var_from():
    msg = "local"  # msg defined in a local namespace
    print(msg)     # In local namespace, you can also access "print" function (Built-in namespace)

var_from()         # displays "local"
print(msg)         # msg not defined in the global namespace, so print function raises NameError
```

As shown in this example, it is possible to access the `var_from` function which is defined in the ***global namespace***, but not `msg` which is defined in the ***local namespace*** of the function! However, it is possible to access the ***global namespace*** from the ***local namespace*** of the function as shown in the following example:

```python
def var_from():
    print(msg)      # msg not defined locally

msg = "global"
var_from()          # but var_from displays "global"
```

In this example, when the Python interpreter evaluates the `var_from` function, it looks for the `msg` identifier in the ***local namespace*** of the function but does not find it. It then follows the **LEGB** rule to browse the following *namespaces* in search of `msg`. There is no ***enclosed namespace*** here, so it searches the ***global namespace*** and finally finds the `msg` identifier that refers to the `'global'` object.

When a function closes another function, we talk about ***enclosing function***. This type of function has its own *namespace* called ***enclosed namespace***. 

<div class="alert alert-block alert-info">
Consider the two functions <code>outer</code> and <code>inner</code> nested below. Execute the next two cells:
</div>

In [ ]:
reset -f

In [ ]:
def outer():           # Enclosed
    msg = "out!"       
    def inner():
       msg = "in!"     # Local
       print('called from inner:', msg)
    inner()
    print('called from outer:', msg)

# Global
msg = 'global'
outer()
print('called from global:', msg)

<div class="alert alert-block alert-info">
<ul>
    <li> Comment the line <code>msg = "in!"</code> then execute the previous code. </li>
    <li> Also comment the line <code>msg = "out!"</code> then run again. </li>
    <li> Conclude. </li>
</ul>
</div>

As you can see, when the instruction `msg = "in!"` is commented, `msg` is equal to `'out!` in the `inner` function. The Python interpreter searches `msg` locally in the `inner` function but does not find it. It then follows the **LEGB** rule up to the level **Enclosed** and finds a variable `msg`.

When the instructions `msg =' in!'` and `msg =' out!'` are commented on, the interpreter finds the variable `msg` neither in `inner` nor in `outer`. It then follows the **LEGB** rule again and goes up to the level of the ***global namespace*** where it finds `msg =' global'`. The `msg` identifier then refers to the `'global'` object in the `outer` and `inner` functions.

## 3. The `global` and `non-local` instructions


As we have seen above, it is possible to access the *namespaces* of higher level ***directly*** (without prefix) according to the rule **LEGB**. Lower level *namespaces* can also share references with higher level *namespaces* using the instructions:

* `non-local`: specifies that the listed identifiers refer to the previously declared identifiers in the lowest ***scope*** surrounding the instruction, **with the exception of global identifiers**,
* `global`: specifies that the listed identifiers must be interpreted as global.


### 3.1. The `non-local` instruction

<div class="alert alert-block alert-info">
To illustrate how the <code>nonlocal</code> instruction works, execute the following two cells:
</div>

In [ ]:
reset -f

In [ ]:
def outer():             # Enclosed
    msg = "out!"
    def inner():         # Local
        nonlocal msg
        msg = 'in!'
        print('called from inner:', msg)
    inner()
    print('called from outer:', msg)

# Global
outer()
print('called from global:', msg)

This may sound a little confusing but the `msg` variable now refers to:

* the object `'in!'` in the ***local namespace*** of `inner`,
* the object `'in!'` in the ***enclosed namespace*** of `outer`,
* nothing in the ***global namespace*** (not defined).

When executing the `inner` function, the `msg` identifier is declared as `non-local`. It locally refers to the object `'in!'`, but its ***scope*** is extended to the lower level namespace surrounding it, i. e. that of the `outer` function. When running `outer`:
* the `msg` identifier refers to the `'out!'` object in line 2,
* then the inner function is defined and called on line 7,
* the `msg` identifier then now refers to the `'in'` object in a non-local way (also impacting the upper namespace, the one of `outer'),
* In line 8, the function <code>print</code> is called on the `msg` identifier which also refers to the `'in!'` object in `outer`.

Note that the `non-local` instruction **does not extend the `msg` *scope* to the global level**. The `msg` variable is therefore not defined in the global namespace, which raises the `NameError` exception. 

<div class="alert alert-block alert-info">
Now invert the lines <b>7</b> and <b>8</b> and conclude.
</div>

### 3.2. The `global` instruction

<div class="alert alert-block alert-info">
To illustrate how the <code>global</code> instruction works, execute the following two cells:
</div>

In [ ]:
reset -f

In [ ]:
def outer():           # Enclosed
    msg = "out!"
    def inner():       # Local
        global msg
        msg = "in!"
        print('called from inner:', msg)
    inner()
    print('called from outer:', msg)

# Global
outer()                
print('called from global:', msg)

As you will have noticed, the `msg` variable now refers to:

* the object `'in!'` in the ***local namespace*** of `inner',
* the object `'out!'` in the ***enclosed namespace*** of `outer`,
* the object `'in!'` in the ***global namespace***.

In the `inner` function, the `msg` identifier is declared as **global**. The Python interpreter looks for the `msg` identifier in the current *namespace* (***local***) and actually finds the one that refers to the `'in!'` object, line 5.

In the `outer` function, when the `print` function is executed in line 8, the Python interpreter looks for the `msg` identifier in the current *namespace* (***enclosed***) and actually finds the one that references the `'out!'` object, line 2. The two `msg` identifiers defined in line 2 and 5 are part of two different *namespaces* and refer to two different objects.

Thanks to the **global** instruction, the scope of the `msg` identifier is extended to the ***global namespace***. The `msg` identifier of line 12 therefore refers to the `'in!'` object defined in `inner`, line 5, since it is global.


<div class="alert alert-block alert-info">
Comment the instruction <code>msg = "out!"</code> in line 2, and execute the code again. Conclude.
</div>

## Summary

* The ***Built-in namespace*** is reserved for the Python interpreter. It essentially consists of the built-in functions.
* A ***Global namespace*** is a namespace in which all identifiers are declared at the main program or module top-level.
* A ***Local namespace*** is created with each function call. An identifier declared in a function is only accessible from that function.
* In the case of nested functions, each function has its own namespace. The namespace of the function enclosing another function is called ***Enclosed namespace***.
* An identifier can exist in several namespaces. These identifiers then (generally) refer to different objects. This avoids collisions.
* The ***scope*** determines the parts of the program from which an identifier can be accessed.  Depending on the location of the identifier in the program, the search is performed in the different namespaces in a specific order determined by the **LEGB** rule.
* The `non-local` instruction is used only in the case of nested functions. It allows to extend the ***scope*** of an identifier to the ***Enclosed namespace***.
* The `global` instruction is classically used in a function. It allows you to define an identifier as part of the ***Global namespace***.

## Application: In the depths of a module

<div class="alert alert-block alert-info">
Create a module named <code>module</code> in which the following function will be implemented:
</div>

```Python
def depths():
    
    dark_depths ='The holy Graal'
    
```

<div class="alert alert-block alert-info">
How to access the variable <code>dark_depths</code> from another file (within the notebook for example)? You can modify the function <code>depths</code> to achieve this, but its behavior must remain the same (returns <code>None</code>).
</div>

## References

* [Python.org - Simple statements](https://docs.python.org/3.8/reference/simple_stmts.html)
* [Confirm.ch - Namespaces](https://blog.confirm.ch/python-namespaces/)
* [data-flair - Namespace & scopes](https://data-flair.training/blogs/python-namespace-and-variable-scope/)